 # Projet web Mining : 
 # FEUDJIO NGOUANET VALDES VOTEL
 # LAGNOL    

### PARTIE 1 : WEB SCRAPING DE LA BASE DE DONNEES

#### installation des packages de base

In [3]:
!wget https://people.irisa.fr/Guillaume.Gravier/teaching/ENSAI/data/francetvinfo.json
!wget https://people.irisa.fr/Guillaume.Gravier/teaching/ENSAI/data/tvinfo-sources.json
!pip install feedparser
!pip install newspaper3k
!python -m spacy download fr_core_news_md

'wget' n'est pas reconnu en tant que commande interne
ou externe, un programme ex�cutable ou un fichier de commandes.
'wget' n'est pas reconnu en tant que commande interne
ou externe, un programme ex�cutable ou un fichier de commandes.



[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


     ---------------------------------------- 0.0/45.8 MB ? eta -:--:--
     ------ --------------------------------- 7.1/45.8 MB 33.6 MB/s eta 0:00:02
     ------------ -------------------------- 14.9/45.8 MB 36.2 MB/s eta 0:00:01
     ----------------- --------------------- 20.7/45.8 MB 33.5 MB/s eta 0:00:01
     ------------------------ -------------- 29.1/45.8 MB 35.5 MB/s eta 0:00:01
     ------------------------------- ------- 36.7/45.8 MB 35.3 MB/s eta 0:00:01
     ----------------------------------- --- 42.2/45.8 MB 33.6 MB/s eta 0:00:01
     --------------------------------------  45.6/45.8 MB 34.5 MB/s eta 0:00:01
     --------------------------------------  45.6/45.8 MB 34.5 MB/s eta 0:00:01
     --------------------------------------  45.6/45.8 MB 34.5 MB/s eta 0:00:01
     --------------------------------------  45.6/45.8 MB 34.5 MB/s eta 0:00:01
     --------------------------------------  45.6/45.8 MB 34.5 MB/s eta 0:00:01
     --------------------------------------  45.


[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


#### Chargement des données deja existantes et des données sur les flus RSS

In [4]:
import json
import ssl
import feedparser as fp

# (a) Se prémunir contre le blocage de commande
ssl._create_default_https_context = ssl._create_unverified_context

# (b) Lire la base de données existante (francetvinfo.json)
with open("francetvinfo.json", "r", encoding="utf-8") as f:
    existing_data = json.load(f)


# (c) Lire les flux RSS listés dans tvinfo-sources.json
with open("tvinfo-sources.json", "r", encoding="utf-8") as f:
    rss_sources = json.load(f)


#### Selection des données qui ne sont pas encore dans la base de données existante

In [5]:
from newspaper import Article

# Extraire les liens existants pour éviter les doublons
existing_links = existing_data.keys()

# Scanner les flux RSS et repérer les nouveaux articles
new_articles = {}

for category, url in rss_sources.items():
    print(f"Lecture du flux RSS : {url}")
    data = fp.parse(url)

    # Parcourir les articles du flux RSS
    for item in data.entries:
        if item.link not in existing_links:  # Vérifier si l'article est nouveau
            try:
                # Utiliser newspaper pour extraire les informations détaillées
                article = Article(item.link)
                article.download()
                article.parse()

                # Ajouter les détails de l'article dans new_articles
                new_articles[item.link] = {
                    "title": article.title or item.title,
                    "date": article.publish_date if article.publish_date else (item.published if hasattr(item, "published") else "N/A"),
                    "author": article.authors or item.get("author", "Inconnu"),
                    "category": category,
                    "content": article.text or item.get("description", "Pas de contenu"),
                    "image_link": article.top_image or "Pas d'image"
                }
            except Exception as e:
                print(f"Erreur lors du traitement de l'article : {item.link}\n{e}")

print(f"{len(new_articles)} nouveaux articles ajoutés :")


Lecture du flux RSS : https://www.francetvinfo.fr/france.rss
Lecture du flux RSS : https://www.francetvinfo.fr/monde/europe.rss
Lecture du flux RSS : https://www.francetvinfo.fr/economie/entreprises.rss
60 nouveaux articles ajoutés :


In [6]:
# On affiche les liens des nouveaux articles parus das la base de données
for key in new_articles.keys():
    print(key)

https://www.francetvinfo.fr/economie/tourisme/les-clients-sont-de-retour-dans-la-region-paca-malgre-l-hiver-les-hoteliers-se-rejouissent-d-une-bonne-annee-touristique_6979166.html#xtor=RSS-3-[general]
https://www.francetvinfo.fr/meteo/cyclone-ouragan/cyclone-chido-a-mayotte/cyclone-chido-la-fondation-de-france-a-deja-collecte-23-millions-d-euros-pour-mayotte-un-elan-de-solidarite-hors-norme_6979448.html#xtor=RSS-3-[general]
https://www.francetvinfo.fr/animaux/jura-le-lynx-une-espece-en-danger_6976448.html#xtor=RSS-3-[general]
https://www.francetvinfo.fr/sports/voile/calvados-un-homme-sauve-apres-16h-a-la-derive_6979328.html#xtor=RSS-3-[general]
https://www.francetvinfo.fr/replay-radio/le-decryptage-eco/hausse-du-chomage-le-ralentissement-du-marche-de-l-emploi-se-confirme-pour-2025_6951746.html#xtor=RSS-3-[general]
https://www.francetvinfo.fr/faits-divers/deux-hommes-mis-en-examen-a-laval-pour-des-soupcons-d-assassinat-d-un-homme-de-30-ans-fin-novembre_6978080.html#xtor=RSS-3-[general]


In [7]:
# faire une nouvelle base de données en y ajoutants de nouvelles données

# Écraser ou initialiser la base
francetvinfo_total = {}  # Réinitialise ou écrase la base existante

# Mettre à jour avec de nouvelles données
francetvinfo_total=existing_data.update(new_articles)

# Afficher la taille de la base
#print(len(francetvinfo_total))


### Extraction d'informations

In [8]:
new_articles

{'https://www.francetvinfo.fr/economie/tourisme/les-clients-sont-de-retour-dans-la-region-paca-malgre-l-hiver-les-hoteliers-se-rejouissent-d-une-bonne-annee-touristique_6979166.html#xtor=RSS-3-[general]': {'title': '"Les clients sont de retour" : en Provence-Alpes-Côte d\'Azur, malgré l\'hiver, les hôteliers se réjouissent d\'une bonne année touristique',
  'date': datetime.datetime(2024, 12, 27, 11, 58, 8, tzinfo=tzoffset(None, 3600)),
  'author': ['David Gonsalvez',
   "Directeur De L'Office Du Tourisme De Bormes-Les-Mimosas"],
  'category': 'france',
  'content': 'La vue depuis la terrasse de l\'hôtel Eden Rose de Bormes-les-Mimosas,dans le Var, est paradisiaque. Entre les vignes, les premiers boutons de mimosas, les toits roses et la mer au loin, les clients s\'émerveillent. "Ça change de la grisaille parisienne ! C\'était le seul refuge en France pour trouver du soleil", glisse un vacancier.\n\nD\'après les premiers chiffres de l\'INSEE sur la saison d\'avril à septembre 2024, pub

In [9]:
import spacy
# Load pipeline and related models
process = spacy.load("fr_core_news_md")
# process text with pipeline

In [10]:
commentaires = [existing_data[key]['content'] for key in existing_data.keys()]
commentaires[0]


'Beaucoup de maires et de secrétaires de mairie ont rencontré au cours de leurs mandats des problèmes de violence, essentiellement verbale. C\'est le cas de Claire. Un jour, un homme est entré dans son bureau et a frappé très fort sur son bureau pour l\'intimider. "J\'ai réagi à l\'instinct, j\'ai essayé de discuter, mais ça s\'est envenimé. Heureusement qu\'une dame est arrivée à la permanence et a menacé d\'appeler la gendarmerie", raconte Claire Carrère-Godebout, maire (SE) de Graveron-Sémerville (Eure).\n\nDes professeurs de karaté et un psychologue\n\nLa plupart de ces élus ne savent pas comment se comporter face à une situation conflictuelle. Alors, l\'Association des maires ruraux de l\'Eure les initie à l\'autodéfense, avec l\'aide de professeurs de karaté. Et un psychologue leur a expliqué comment désamorcer un différent. "C\'est nécessaire qu\'ils aient confiance en eux donc, à partir de là, je pense que cet atelier ne peut avoir que des bénéfices", explique Christophe Micaux

In [11]:
import spacy
# chargement un modèle linguistique pré-entraîné pour le français et on le stocke dans process.
process = spacy.load("fr_core_news_md")
# list e that were detected
for element in commentaires :
    res = process(element)
    for e in res.ents:
        print(e.text, e.start, e.end, e.label_)

Claire 28 29 PER
Claire Carrère-Godebout 91 95 PER
SE 98 99 LOC
Graveron-Sémerville 101 104 LOC
Eure 105 106 LOC
Association des maires ruraux de l'Eure 137 144 ORG
Christophe Micaux 200 202 PER
AlertePollution Rivières 1 3 LOC
Cliquez 21 22 LOC
!

 26 28 MISC
Victor 36 37 MISC
Pygargue 39 40 LOC
Haliaeetus 44 45 LOC
massif du Mont-Blanc 50 53 LOC
Europe 59 60 LOC
Alpes 167 168 LOC
Victor 182 183 PER
Jacques-Olivier Travers 197 201 PER
Antarctique 289 290 LOC
Amazonie 293 294 LOC
Alpes 309 310 LOC
glacier des Bossons 337 340 LOC
Alpes 381 382 LOC
AlertePollution Rivières 1 3 LOC
Cliquez 21 22 LOC
massif du Mont-Blanc 81 84 LOC
Chamonix 118 119 LOC
Philippe Batoux 120 122 PER
Ludovic Ravanel 123 125 PER
CNRS 131 132 ORG
Philippe Batoux 192 194 PER
massif du Mont-Blanc 261 264 LOC
Ça 265 266 MISC
Chez les alpinistes 280 283 MISC
chaîne des Alpes 4 7 LOC
Europe 19 20 LOC
le Mont-Blanc 22 24 LOC
département de la Haute-Savoie 59 63 LOC
France 65 66 LOC
vallée d'Aoste 69 72 LOC
Italie 74 75

In [12]:
res.ents

(Rémunération,
 Sarah,
 Robert Walters,
 Sarah Lemoine,
 Coralie Rachet,
 Robert Walters,
 Coralie Rachet,
 Robert Walters,
 Coralie Rachet)

In [29]:
import spacy
from collections import Counter

# Charger le modèle spaCy avec les composants nécessaires
nlp = spacy.load("fr_core_news_md", disable=["tagger"])  # Garder 'parser' pour segmentation en phrases

# Liste contenant les contenus des articles et leurs liens
commentaires = {
    key: existing_data[key]['content']
    for key in existing_data.keys()
}

# Dictionnaire pour stocker les entités extraites par lien
resultats = {}

# Compteur global pour stocker les fréquences des entités
entite_counter = Counter()

# Utilisation de nlp.pipe pour traiter les articles efficacement
for key, doc in zip(commentaires.keys(), nlp.pipe(commentaires.values(), batch_size=20, n_process=2)):
    entities = []
    sentences = []

    # Extraire les entités pour le document
    for ent in doc.ents:
        entities.append({
            "text": ent.text,   # Texte de l'entité
            "type": ent.label_,  # Type d'entité (PER, LOC, ORG, etc.)
            "start": ent.start_char,
            "end": ent.end_char
        })
        entite_counter[ent.text] += 1  # Compter la fréquence de l'entité globale

    # Parcourir les phrases et associer les entités
    for sent in doc.sents:
        sentence_entities = [
            {"text": ent.text, "type": ent.label_}
            for ent in sent.ents
        ]
        sentences.append({
            "text": sent.text,
            "entities": sentence_entities
        })

    # Stocker les entités et les phrases pour chaque document
    resultats[key] = {
        "entities": entities,
        "sentences": sentences
    }

# Obtenir les 20 entités les plus représentées
top_20_entites = entite_counter.most_common(20)

# Affichage des résultats
print("Top 20 entités les plus représentées :")
print()
for ent, freq in top_20_entites:
    print(f"{ent} : {freq} occurrences")

# Affichage des phrases et des entités associées pour vérification
print("\nExemple de segmentation et entités par phrase :")
for key, data in resultats.items():
    print(f"\nDocument: {key}")
    for sentence in data["sentences"]:
        print(f"Phrase: {sentence['text']}")
        print(f"Entités: {sentence['entities']}")
    break  # Limiter l'affichage à un document pour éviter de surcharger




Top 20 entités les plus représentées :

JT : 2082 occurrences
France : 823 occurrences
Covid-19 : 789 occurrences
Allemagne : 569 occurrences
Français : 415 occurrences
la France : 400 occurrences
Paris : 388 occurrences
franceinfo : 364 occurrences
Europe : 327 occurrences
Union européenne : 318 occurrences
État : 296 occurrences
Royaume-Uni : 260 occurrences
Italie : 256 occurrences
Emmanuel Macron : 255 occurrences
Etat : 236 occurrences
Brexit : 232 occurrences
UE : 218 occurrences
Grèce : 203 occurrences
Chine : 198 occurrences
l'Europe : 196 occurrences

Exemple de segmentation et entités par phrase :

Document: https://www.francetvinfo.fr/sante/prevention/eure-quand-les-elus-apprennent-a-se-defendre_3791635.html#xtor=RSS-3-[france]
Phrase: Beaucoup de maires et de secrétaires de mairie ont rencontré au cours de leurs mandats des problèmes de violence, essentiellement verbale.
Entités: []
Phrase: C'est le cas de Claire.
Entités: [{'text': 'Claire', 'type': 'PER'}]
Phrase: Un jour

In [30]:

# Afficher les entités par article
print("\nEntités extraites par article :")
print()
for link, data in resultats.items():
    print(f"\nArticle : {link}")
    for ent in data['entities']:
        print(f" - Texte: {ent['text']}, Type: {ent['type']}, Span: ({ent['start']}, {ent['end']})")


Entités extraites par article :


Article : https://www.francetvinfo.fr/sante/prevention/eure-quand-les-elus-apprennent-a-se-defendre_3791635.html#xtor=RSS-3-[france]
 - Texte: Claire, Type: PER, Span: (155, 161)
 - Texte: Claire Carrère-Godebout, Type: PER, Span: (437, 460)
 - Texte: SE, Type: LOC, Span: (469, 471)
 - Texte: Graveron-Sémerville, Type: LOC, Span: (476, 495)
 - Texte: Eure, Type: LOC, Span: (497, 501)
 - Texte: Association des maires ruraux de l'Eure, Type: ORG, Span: (653, 692)
 - Texte: Christophe Micaux, Type: PER, Span: (964, 981)

Article : https://www.francetvinfo.fr/france/video-sur-le-dos-d-un-aigle-pecheur-au-dessus-du-massif-du-mont-blanc-dont-les-glaciers-fondent-aujourd-hui-a-vue-d-oeil_3791583.html#xtor=RSS-3-[france]
 - Texte: AlertePollution Rivières, Type: LOC, Span: (1, 25)
 - Texte: Cliquez, Type: LOC, Span: (121, 128)
 - Texte: !

, Type: MISC, Span: (151, 154)
 - Texte: Victor, Type: MISC, Span: (204, 210)
 - Texte: Pygargue, Type: LOC, Span: (215, 

In [31]:
resultats

{'https://www.francetvinfo.fr/sante/prevention/eure-quand-les-elus-apprennent-a-se-defendre_3791635.html#xtor=RSS-3-[france]': {'entities': [{'text': 'Claire',
    'type': 'PER',
    'start': 155,
    'end': 161},
   {'text': 'Claire Carrère-Godebout',
    'type': 'PER',
    'start': 437,
    'end': 460},
   {'text': 'SE', 'type': 'LOC', 'start': 469, 'end': 471},
   {'text': 'Graveron-Sémerville', 'type': 'LOC', 'start': 476, 'end': 495},
   {'text': 'Eure', 'type': 'LOC', 'start': 497, 'end': 501},
   {'text': "Association des maires ruraux de l'Eure",
    'type': 'ORG',
    'start': 653,
    'end': 692},
   {'text': 'Christophe Micaux', 'type': 'PER', 'start': 964, 'end': 981}],
  'sentences': [{'text': 'Beaucoup de maires et de secrétaires de mairie ont rencontré au cours de leurs mandats des problèmes de violence, essentiellement verbale.',
    'entities': []},
   {'text': "C'est le cas de Claire.",
    'entities': [{'text': 'Claire', 'type': 'PER'}]},
   {'text': "Un jour, un hom

In [32]:
from collections import Counter

# Initialiser les compteurs pour chaque type d'entité
person_counter = Counter()
org_counter = Counter()
loc_counter = Counter()

# Parcourir les résultats et compter les entités par type
for lien, contenu in resultats.items():
    for ent in contenu['entities']:
        if ent['type'] == 'PER':  # Personnes
            person_counter[ent['text']] += 1
        elif ent['type'] == 'ORG':  # Organisations
            org_counter[ent['text']] += 1
        elif ent['type'] == 'LOC':  # Lieux
            loc_counter[ent['text']] += 1

# Obtenir les 20 entités les plus fréquentes pour chaque type
top_persons = person_counter.most_common(20)
top_organizations = org_counter.most_common(20)
top_locations = loc_counter.most_common(20)

# Stocker les résultats dans des listes
persons_list = [ent for ent, freq in top_persons]
organizations_list = [ent for ent, freq in top_organizations]
locations_list = [ent for ent, freq in top_locations]

# Afficher les résultats
print("Top 20 des entités de type PERSON :")
for ent, freq in top_persons:
    print(f"{ent}: {freq}")

print("\nTop 20 des entités de type ORG :")
for ent, freq in top_organizations:
    print(f"{ent}: {freq}")

print("\nTop 20 des entités de type LOC :")
for ent, freq in top_locations:
    print(f"{ent}: {freq}")

# Résumé des listes
print("\nListes des entités les plus fréquentes :")
print(f"Personnes : {persons_list}")
print(f"Organisations : {organizations_list}")
print(f"Lieux : {locations_list}")

Top 20 des entités de type PERSON :
Emmanuel Macron: 255
Bruno Le Maire: 123
Angela Merkel: 118
président de la République: 63
Boris Johnson: 55
Laurent Desbonnets: 50
Muriel Pénicaud: 48
Thierry Breton: 44
Donald Trump: 42
Ursula von der Leyen: 41
Edouard Philippe: 37
Birkenau: 35
Olivier Véran: 33
César: 27
George Floyd: 27
Vladimir Poutine: 26
Michel Barnier: 26
Valéry Lerouge: 26
Christophe Castaner: 24
Jérôme Salomon: 24

Top 20 des entités de type ORG :
JT: 2082
franceinfo: 360
Union européenne: 318
Brexit: 226
UE: 218
AFP: 157
France Télévisions: 129
Commission européenne: 106
Renault: 96
MAXPPP: 79
CGT: 73
Magazines: 67
Alstom: 62
ministre de la Santé: 60
Amazon: 56
Airbus: 49
LREM: 48
Medef: 46
Travail: 42
Parlement: 41

Top 20 des entités de type LOC :
France: 823
Allemagne: 569
la France: 400
Paris: 388
Français: 342
Europe: 327
État: 296
Royaume-Uni: 260
Italie: 256
Etat: 236
Grèce: 202
Chine: 198
l'Europe: 196
Turquie: 167
Bruxelles: 153
Londres: 145
Berlin: 134
Espagne: 1

In [33]:
# Afficher les résultats
print("Top 20 des entités de type PERSON et leur occurence:")
top_persons 

Top 20 des entités de type PERSON et leur occurence:


[('Emmanuel Macron', 255),
 ('Bruno Le Maire', 123),
 ('Angela Merkel', 118),
 ('président de la République', 63),
 ('Boris Johnson', 55),
 ('Laurent Desbonnets', 50),
 ('Muriel Pénicaud', 48),
 ('Thierry Breton', 44),
 ('Donald Trump', 42),
 ('Ursula von der Leyen', 41),
 ('Edouard Philippe', 37),
 ('Birkenau', 35),
 ('Olivier Véran', 33),
 ('César', 27),
 ('George Floyd', 27),
 ('Vladimir Poutine', 26),
 ('Michel Barnier', 26),
 ('Valéry Lerouge', 26),
 ('Christophe Castaner', 24),
 ('Jérôme Salomon', 24)]

In [34]:
print("\nTop 20 des entités de type ORG et leur occurence:")
top_organizations 


Top 20 des entités de type ORG et leur occurence:


[('JT', 2082),
 ('franceinfo', 360),
 ('Union européenne', 318),
 ('Brexit', 226),
 ('UE', 218),
 ('AFP', 157),
 ('France Télévisions', 129),
 ('Commission européenne', 106),
 ('Renault', 96),
 ('MAXPPP', 79),
 ('CGT', 73),
 ('Magazines', 67),
 ('Alstom', 62),
 ('ministre de la Santé', 60),
 ('Amazon', 56),
 ('Airbus', 49),
 ('LREM', 48),
 ('Medef', 46),
 ('Travail', 42),
 ('Parlement', 41)]

In [35]:
print("\nTop 20 des entités de type LOC et leur occurence:")
top_locations 


Top 20 des entités de type LOC et leur occurence:


[('France', 823),
 ('Allemagne', 569),
 ('la France', 400),
 ('Paris', 388),
 ('Français', 342),
 ('Europe', 327),
 ('État', 296),
 ('Royaume-Uni', 260),
 ('Italie', 256),
 ('Etat', 236),
 ('Grèce', 202),
 ('Chine', 198),
 ("l'Europe", 196),
 ('Turquie', 167),
 ('Bruxelles', 153),
 ('Londres', 145),
 ('Berlin', 134),
 ('Espagne', 130),
 ('Européens', 117),
 ('Franceinfo', 113)]

### Question 10

In [36]:
def compter_cooccurrences(collection, entite1, type1, entite2, type2):
    """
    Compte le nombre de co-occurrences de deux entités (avec leurs types) dans une collection de documents.

    Args:
        collection (dict): Un dictionnaire contenant les documents avec leurs entités.
        entite1 (str): La première entité.
        type1 (str): Le type de la première entité (ex: 'PER', 'ORG', 'LOC').
        entite2 (str): La deuxième entité.
        type2 (str): Le type de la deuxième entité (ex: 'PER', 'ORG', 'LOC').

    Returns:
        int: Le nombre de documents où les deux entités coexistent.
    """
    cooccurrence_count = 0

    # Parcourir chaque document dans la collection
    for doc_id, contenu in collection.items():
        entities_in_doc = contenu['entities']  # Liste des entités dans le document
        # Vérifier si les deux entités apparaissent dans le même document
        found_entite1 = any(ent['text'] == entite1 and ent['type'] == type1 for ent in entities_in_doc)
        found_entite2 = any(ent['text'] == entite2 and ent['type'] == type2 for ent in entities_in_doc)
        
        # Si les deux entités sont présentes, incrémenter le compteur
        if found_entite1 and found_entite2:
            cooccurrence_count += 1

    return cooccurrence_count


In [37]:
# Ici nous faisons un exemple avec Francois Bayrou qui est une entité personne et Mayotte qui est une entité localisation
cooccurrences = compter_cooccurrences(resultats, 'François Bayrou', 'PER', 'Mayotte', 'LOC')

# Affichage du résultat
print(f"Nombre de co-occurrences entre 'François Bayrou' (PER) et 'Mayotte' (LOC) : {cooccurrences}")

Nombre de co-occurrences entre 'François Bayrou' (PER) et 'Mayotte' (LOC) : 1


### Question 11

In [38]:
from itertools import combinations
# Stocker les résultats des entités dans des listes
persons_list = [ent for ent, _ in top_persons]
organizations_list = [ent for ent, _ in top_organizations]
locations_list = [ent for ent, _ in top_locations]

# Liste des paires d'entités à vérifier (en évitant les paires du même type)
pairs = []

# Créer des paires d'entités entre les différentes catégories, mais sans dupliquer le type
pairs += [(p, o) for p in persons_list for o in organizations_list]  # Paires entre personnes et organisations
pairs += [(p, l) for p in persons_list for l in locations_list]  # Paires entre personnes et lieux
pairs += [(o, l) for o in organizations_list for l in locations_list]  # Paires entre organisations et lieux

# Compter les co-occurrences pour chaque paire
cooccurrences_results = {}

for ent1, ent2 in pairs:
    type1 = 'PER' if ent1 in persons_list else 'ORG' if ent1 in organizations_list else 'LOC'
    type2 = 'PER' if ent2 in persons_list else 'ORG' if ent2 in organizations_list else 'LOC'
    cooccurrences_results[(ent1, ent2)] = compter_cooccurrences(resultats, ent1, type1, ent2, type2)

# Trier les résultats par le nombre de co-occurrences, en ordre décroissant
top_cooccurrences = Counter(cooccurrences_results).most_common(2)

# Affichage des deux paires les plus fréquentes
print("Les deux paires d'entités les plus fréquentes sont :")
for pair, count in top_cooccurrences:
    print(f"Paire : {pair}, Co-occurrences : {count}")

Les deux paires d'entités les plus fréquentes sont :
Paire : ('JT', 'France'), Co-occurrences : 200
Paire : ('JT', 'Allemagne'), Co-occurrences : 159


### Question 12

In [43]:
def compter_cooccurrences_par_phrase(collection, entite1, type1, entite2, type2):
    """
    Compte le nombre de phrases où deux entités (avec leurs types) coexistent.

    Args:
        collection (dict): Un dictionnaire contenant les documents avec leurs entités et les phrases.
        entite1 (str): La première entité.
        type1 (str): Le type de la première entité (ex: 'PER', 'ORG', 'LOC').
        entite2 (str): La deuxième entité.
        type2 (str): Le type de la deuxième entité (ex: 'PER', 'ORG', 'LOC').

    Returns:
        int: Le nombre de phrases où les deux entités coexistent.
    """
    cooccurrence_count = 0

    # Parcourir chaque document dans la collection
    for doc_id, contenu in collection.items():
        sentences = contenu['sentences']  # Liste des phrases (chacune est un span du document)
        
        # Parcourir chaque phrase pour trouver les co-occurrences
        for sentence in sentences:
            entities_in_sentence = sentence['entities']  # Liste des entités dans la phrase
            
            # Vérifier si les deux entités apparaissent dans la même phrase
            found_entite1 = any(ent['text'] == entite1 and ent['type'] == type1 for ent in entities_in_sentence)
            found_entite2 = any(ent['text'] == entite2 and ent['type'] == type2 for ent in entities_in_sentence)
            
            # Si les deux entités sont présentes dans la phrase, incrémenter le compteur
            if found_entite1 and found_entite2:
                cooccurrence_count += 1

    return cooccurrence_count


In [44]:
cooccurrences = compter_cooccurrences_par_phrase(resultats, 'François Bayrou', 'PER', 'Mayotte', 'LOC')

# Affichage du résultat
print(f"Nombre de co-occurrences entre 'François Bayrou' (PER) et 'Mayotte' (LOC) : {cooccurrences}")

Nombre de co-occurrences entre 'François Bayrou' (PER) et 'Mayotte' (LOC) : 0


### Question 13